# VacationPy
----

#### Note
* Keep an eye on your API usage. Use https://developers.google.com/maps/reporting/gmp-reporting as reference for how to monitor your usage and billing.

* Instructions have been included for each segment. You do not have to follow them exactly, but they are included to help you think through the steps.

In [2]:
# Dependencies and Setup
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import gmaps
import os
import json

# Import API key
from api_keys import g_key

### Store Part I results into DataFrame
* Load the csv exported in Part I to a DataFrame

In [3]:
vacation_path = 'output_data/city_weather_data.csv'
vacation_df = pd.read_csv(vacation_path)
vacation_df.head

<bound method NDFrame.head of             City Country          Date  Latitude  Longitude  Cloudiness (%)  \
0        mataura      NZ  1.629351e+09  -46.1927   168.8643           100.0   
1        rikitea      PF  1.629351e+09  -23.1203  -134.9692           100.0   
2          sitka      US  1.629351e+09   57.0531  -135.3300            90.0   
3    barentsburg     NaN           NaN       NaN        NaN             NaN   
4      busselton      AU  1.629351e+09  -33.6500   115.3333            93.0   
..           ...     ...           ...       ...        ...             ...   
624      ganzhou      CN  1.629351e+09   28.8184   115.4327            76.0   
625         seka      TH  1.629351e+09   17.9285   103.9552            79.0   
626   port keats      AU  1.629351e+09  -14.2500   129.5500             0.0   
627        genhe      CN  1.629351e+09   50.7833   121.5167           100.0   
628      saquena      PE  1.629351e+09   -4.6667   -73.5167            38.0   

     Humidity  Maximu

### Humidity Heatmap
* Configure gmaps.
* Use the Lat and Lng as locations and Humidity as the weight.
* Add Heatmap layer to map.

In [4]:
gmaps.configure(api_key=g_key)

In [5]:
# Store 'Lat' and 'Lng' into  locations 
locations = vacation_df[["Latitude", "Longitude"]].astype(float)

# Convert humidity to float and store
# HINT: be sure to handle NaN values
vacation_df = vacation_df.dropna()
humidity = vacation_df.Humidity.astype(float)

# Create a poverty Heatmap layer
fig = gmaps.figure()

heat_layer = gmaps.heatmap_layer(locations, weights=humidity, 
                                 dissipating=False, max_intensity=100,
                                 point_radius = 5)

fig.add_layer(heat_layer)

fig

ValueError: weights must be of the same length as locations or None

### Create new DataFrame fitting weather criteria
* Narrow down the cities to fit weather conditions.
* Drop any rows will null values.

In [11]:
best_temp = vacation_df ['Maximum Temperature (F)'] < 90
best_temp = vacation_df ['Maximum Temperature (F)'] > 55
best_wind = vacation_df ['Wind Speed (mph)'] < 10
best_cloudiness = vacation_df ['Cloudiness (%)'] > 60
best_fog = vacation_df ['Humidity'] > 60
my_weather = best_temp & best_wind & best_cloudiness & best_fog

# Extra: Drop the rows with nulls
bunk_vacations = vacation_df[my_weather]
bunk_vacations = bunk_vacations.dropna()
bunk_vacations = bunk_vacations.reset_index()
bunk_vacations.head()

index       City Country          Date  Latitude  Longitude  \
0      1    rikitea      PF  1.629351e+09  -23.1203  -134.9692   
1      2      sitka      US  1.629351e+09   57.0531  -135.3300   
2      4  busselton      AU  1.629351e+09  -33.6500   115.3333   
3     12      vaini      TO  1.629351e+09  -21.2000  -175.2000   
4     15      tiksi      RU  1.629351e+09   71.6872   128.8694   

   Cloudiness (%)  Humidity  Maximum Temperature (F)  Wind Speed (mph)  
0           100.0      69.0                   69.746              9.80  
1            90.0      82.0                   57.362              3.09  
2            93.0      79.0                   60.314              4.47  
3            75.0     100.0                   73.832              3.60  
4           100.0      81.0                   55.490              5.03

### Hotel Map
* Store into variable named `hotel_df`.
* Add a "Hotel Name" column to the DataFrame.
* Set parameters to search for hotels with 5000 meters.
* Hit the Google Places API for each city's coordinates.
* Store the first Hotel result into the DataFrame.
* Plot markers on top of the heatmap.

In [12]:
# Create a hotel DataFrame and add a column for hotel name
hotel_df = pd.DataFrame(bunk_vacations, columns=['City', 'Country', 'Latitude', 'Longitude', 'Maximum Temperature (F)', 'Hotel Name'])
hotel_df.head()

City Country  Latitude  Longitude  Maximum Temperature (F)  Hotel Name
0    rikitea      PF  -23.1203  -134.9692                   69.746         NaN
1      sitka      US   57.0531  -135.3300                   57.362         NaN
2  busselton      AU  -33.6500   115.3333                   60.314         NaN
3      vaini      TO  -21.2000  -175.2000                   73.832         NaN
4      tiksi      RU   71.6872   128.8694                   55.490         NaN

In [13]:
counter = 0

for index, row in hotel_df.iterrows():

    # Set parameters to search for hotels with 5000 meters.
    params = {"location": f"{row['Latitude']}, {row['Longitude']}", "radius": 5000, "types": "lodging",
              "keyword": "Hotel", "key": g_key}
    # base url
    base_url = "https://maps.googleapis.com/maps/api/place/nearbysearch/json"

    # run a json response with the parameters above
    response = requests.get(base_url, params=params)
    
    # convert to json and print them easy to read
    response_j = response.json()
    print(json.dumps(response_j, indent=4, sort_keys=True))
    
    results = response_j['results']
    
    # Name the hotel if you get a positive result
    if len(results) > 0:
        name = response_j['results'][0]['name']
        hotel_df.iloc[counter, -1] = name
    counter = counter + 1

hotel_bunk_df = hotel_df
hotel_bunk_df

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -23.1206197,
                    "lng": -134.9687529
                },
                "viewport": {
                    "northeast": {
                        "lat": -23.11945897010728,
                        "lng": -134.9673878201073
                    },
                    "southwest": {
                        "lat": -23.12215862989272,
                        "lng": -134.9700874798928
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "icon_background_color": "#909CE1",
            "icon_mask_base_uri": "https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet",
            "name": "People ThankYou",
            "opening_hours": {
                "open_now": true
         

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -33.6596926,
                    "lng": 115.2786132
                },
                "viewport": {
                    "northeast": {
                        "lat": -33.65853142010727,
                        "lng": 115.2800527798927
                    },
                    "southwest": {
                        "lat": -33.66123107989272,
                        "lng": 115.2773531201073
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "icon_background_color": "#909CE1",
            "icon_mask_base_uri": "https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet",
            "name": "The Sebel Busselton",
            "opening_hours": {
                "open_now": true
        

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -21.1553145,
                    "lng": -175.1771504
                },
                "viewport": {
                    "northeast": {
                        "lat": -21.15379937010728,
                        "lng": -175.1758084201073
                    },
                    "southwest": {
                        "lat": -21.15649902989272,
                        "lng": -175.1785080798927
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "icon_background_color": "#909CE1",
            "icon_mask_base_uri": "https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet",
            "name": "Paradise First Hotel",
            "place_id": "ChIJB52qqu6j9HERTiGNr106F1I",
            "

{
    "html_attributions": [],
    "results": [],
    "status": "ZERO_RESULTS"
}
{
    "html_attributions": [],
    "next_page_token": "Aap_uEA0YITzgoRyZwdaKe2JgdP94ax--C_7K0XSTxtHR8Sh_cAzvLTBQ7hl4CVsklTz8kD-hqzw-MyheLFaqW41tz-v4HMLvABMqqlJ12ISKBNahm3zz0BDJY0Mm5kgescVtA_D_Ayud1usHOYWXrs68-twZQ9fH1yjf0DLjEUA7EgK1M7R5KYXnykwW-zXxfwKoymQyEsoPq-0X53Fm0A6_vFbRCFVpplYz3CRzKKgMG2sdkOMb6cloBOiMiSzGc1F0WFLS_X_S9ImcLs5ehrK2L6TUXdb7BsJNysAC3stCm85YQWEX52TXlddE65LUKRWlaelnN4RMMF4_DcnKrm4duTgKlvBfIGBmwqmCK2aUqi-M84vh3EECuiCM-UwPvk3Bdr3X8R2p8TFDvZN-I_RGGNf4s2Y5F7qHCcum9aBe7qVI0d1ElDa-VdkWaIwaOwQmg",
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -33.92358,
                    "lng": 18.379375
                },
                "viewport": {
                    "northeast": {
                        "lat": -33.92191527010728,
                        "lng": 18.38073142989272
                   

{
    "html_attributions": [],
    "results": [],
    "status": "ZERO_RESULTS"
}
{
    "html_attributions": [],
    "next_page_token": "Aap_uEA65dKXfv4gczM0WPJnDemT3oHbRWht2RvrxrgcE7J9xUHTNW6amEDqaEarAydxVJlgI1lgh42bAlf-7RJXtsAFE-R_4FnUqsvSeqhd8YL4tfyjuEdyFqC_H1ksS9qwO8lwlFCtuAqYtaU9mn28482oUXoyqpmo2RIsqYmWoTodLpUhGrKAWRmHJ-wyEhDWWtvwkR5Aa5s0r2nDP9MfIDhYLjuq84QGc8D2VdvRZvcqhdAsBeM-02f5fMlJIClrFrvjBwif7GEUze1a0HHukaiaFdLIYTrA-xWLc74uXUygH3cScrelTbmH3ag5ufFwPmGXZ9WbTJZiDpmXHULlx967uJliU5uFsTFBEIXdiO0lhKMALnBwgG2ZpAQYW5m2Rq9g2g-ZyODVZHe3itnCJrCP3_UMY1obQnOfzv9mGJXwevIFKnlZ4Q2AJSvUludPLA",
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 24.7255095,
                    "lng": 121.7625515
                },
                "viewport": {
                    "northeast": {
                        "lat": 24.72678507989272,
                        "lng": 121.7637400298927
                 

...

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 49.16079000000001,
                    "lng": 125.2236899
                },
                "viewport": {
                    "northeast": {
                        "lat": 49.16215072989272,
                        "lng": 125.2251765298927
                    },
                    "southwest": {
                        "lat": 49.15945107010727,
                        "lng": 125.2224768701073
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "icon_background_color": "#909CE1",
            "icon_mask_base_uri": "https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet",
            "name": "Dong Fang Hui Business Hotel",
            "place_id": "ChIJM_t5j0WrY14RB-fjpOE-UCE",
    

{
    "html_attributions": [],
    "results": [],
    "status": "ZERO_RESULTS"
}
{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 37.7147319,
                    "lng": -25.469431
                },
                "viewport": {
                    "northeast": {
                        "lat": 37.71635042989272,
                        "lng": -25.46789047010728
                    },
                    "southwest": {
                        "lat": 37.71365077010728,
                        "lng": -25.47059012989272
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "icon_background_color": "#909CE1",
            "icon_mask_base_uri": "https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet",
            "name": "Pestana Bahia P

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -15.4315949,
                    "lng": -74.61676469999999
                },
                "viewport": {
                    "northeast": {
                        "lat": -15.43025477010728,
                        "lng": -74.61538387010728
                    },
                    "southwest": {
                        "lat": -15.43295442989272,
                        "lng": -74.61808352989271
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "icon_background_color": "#909CE1",
            "icon_mask_base_uri": "https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet",
            "name": "HOSPEDAJE XIMENA",
            "opening_hours": {
                "open_now": true
  

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 44.1962646,
                    "lng": -77.0588094
                },
                "viewport": {
                    "northeast": {
                        "lat": 44.19764562989272,
                        "lng": -77.05746547010727
                    },
                    "southwest": {
                        "lat": 44.19494597010727,
                        "lng": -77.06016512989271
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "icon_background_color": "#909CE1",
            "icon_mask_base_uri": "https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet",
            "name": "Bayview Inn Motel & Restaurant",
            "opening_hours": {
                "open_now": fal

City Country  Latitude  Longitude  \
0                 rikitea      PF  -23.1203  -134.9692   
1                   sitka      US   57.0531  -135.3300   
2               busselton      AU  -33.6500   115.3333   
3                   vaini      TO  -21.2000  -175.2000   
4                   tiksi      RU   71.6872   128.8694   
..                    ...     ...       ...        ...   
193  vila franca do campo      PT   37.7167   -25.4333   
194                 acari      PE  -15.4311   -74.6158   
195             deseronto      CA   44.2001   -77.0494   
196               ganzhou      CN   28.8184   115.4327   
197                 genhe      CN   50.7833   121.5167   

     Maximum Temperature (F)                      Hotel Name  
0                     69.746                 People ThankYou  
1                     57.362        Super 8 by Wyndham Sitka  
2                     60.314             The Sebel Busselton  
3                     73.832            Paradise First Hotel  
4                     55.490                         Arktika  
..                       ...                             ...  
193                   74.084             Pestana Bahia Praia  
194                   63.500                HOSPEDAJE XIMENA  
195                   71.600  Bayview Inn Motel & Restaurant  
196                   88.052                             NaN  
197                   61.484               Forest Snow Hotel  

[198 rows x 6 columns]

In [15]:
# NOTE: Do not change any of the code in this cell

# Using the template add the hotel marks to the heatmap
info_box_template = """
<dl>
<dt>Name</dt><dd>{Hotel Name}</dd>
<dt>City</dt><dd>{City}</dd>
<dt>Country</dt><dd>{Country}</dd>
</dl>
"""
# Store the DataFrame Row
# NOTE: be sure to update with your DataFrame name
hotel_info = [info_box_template.format(**row) for index, row in hotel_df.iterrows()]
locations = hotel_df[["Latitude", "Longitude"]]

In [16]:
# Add marker layer ontop of heat map
marker_layer = gmaps.marker_layer(locations, info_box_content=hotel_info)

# Display figure
fig.add_layer(marker_layer)
fig.add_layer(heat_layer)
fig

NameError: name 'heat_layer' is not defined